In [1]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

# Imports
import numpy as np
import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)

# Our application logic will be added here



In [2]:
def cnn_model_fn(features, labels, mode):
  """Model function for CNN."""
  # Input Layer
  input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

  # Convolutional Layer #1
  conv1 = tf.layers.conv2d(
      inputs=input_layer,
      filters=32,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #1
  pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

  # Convolutional Layer #2 and Pooling Layer #2
  conv2 = tf.layers.conv2d(
      inputs=pool1,
      filters=64,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)
  pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

  # Dense Layer
  pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])
  dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)
  dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

  # Logits Layer
  logits = tf.layers.dense(inputs=dropout, units=10)

  predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
  }

  if mode == tf.estimator.ModeKeys.PREDICT:
    return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

  # Calculate Loss (for both TRAIN and EVAL modes)
  loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

  # Configure the Training Op (for TRAIN mode)
  if mode == tf.estimator.ModeKeys.TRAIN:
    optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
    train_op = optimizer.minimize(
        loss=loss,
        global_step=tf.train.get_global_step())
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

  # Add evaluation metrics (for EVAL mode)
  eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"])}
  return tf.estimator.EstimatorSpec(
      mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

In [3]:
def main(unused_argv):
  # Load training and eval data
  mnist = tf.contrib.learn.datasets.load_dataset("mnist")
  train_data = mnist.train.images # Returns np.array
  train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
  eval_data = mnist.test.images # Returns np.array
  eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)
  
  # Create the Estimator
  mnist_classifier = tf.estimator.Estimator(model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")
  
  # Set up logging for predictions
  tensors_to_log = {"probabilities": "softmax_tensor"}
  logging_hook = tf.train.LoggingTensorHook(tensors=tensors_to_log, every_n_iter=50)

  # Train the model
  train_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": train_data},
    y=train_labels,
    batch_size=100,
    num_epochs=None,
    shuffle=True)
  mnist_classifier.train(
    input_fn=train_input_fn,
    steps=20000,
    hooks=[logging_hook])
    
  # Evaluate the model and print results
  eval_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": eval_data},
    y=eval_labels,
    num_epochs=1,
    shuffle=False)
  eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
  print(eval_results)

In [4]:
if __name__ == "__main__":
  tf.app.run()

Successfully downloaded train-images-idx3-ubyte.gz 9912422 bytes.
Extracting MNIST-data/train-images-idx3-ubyte.gz
Successfully downloaded train-labels-idx1-ubyte.gz 28881 bytes.
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Successfully downloaded t10k-images-idx3-ubyte.gz 1648877 bytes.
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Successfully downloaded t10k-labels-idx1-ubyte.gz 4542 bytes.
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': '/tmp/mnist_convnet_model', '_save_checkpoints_steps': None, '_tf_random_seed': 1, '_save_summary_steps': 100, '_keep_checkpoint_max': 5, '_log_step_count_steps': 100, '_keep_checkpoint_every_n_hours': 10000, '_session_config': None, '_save_checkpoints_secs': 600}
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Saving checkpoints for 1 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:probabilities = [[ 0.10048153  0.10619328  0.08548912  0.1

INFO:tensorflow:step = 1, loss = 2.30556
INFO:tensorflow:probabilities = [[ 0.09428517  0.12315702  0.07508824  0.10417884  0.10203977  0.09223295
   0.09197199  0.10169654  0.09449057  0.12085903]
 [ 0.08307787  0.10356259  0.08159544  0.1037145   0.10681396  0.09913222
   0.10842752  0.09318973  0.09974585  0.12074032]
 [ 0.08529635  0.12294046  0.09048207  0.10254668  0.09761282  0.09573239
   0.0993878   0.0825518   0.10149451  0.12195514]
 [ 0.0915979   0.1121478   0.08230747  0.10341706  0.10500871  0.08775432
   0.11168201  0.09272376  0.09496342  0.11839759]
 [ 0.09769977  0.10101816  0.08138186  0.11024378  0.11300898  0.09720022
   0.1159298   0.08504978  0.08778228  0.11068539]
 [ 0.08903994  0.11164222  0.08246978  0.0966425   0.10895047  0.08883905
   0.10389788  0.11184349  0.09474024  0.11193445]
 [ 0.10177225  0.10518754  0.09776884  0.10831822  0.0902117   0.08711261
   0.10587464  0.10650827  0.09333577  0.10391012]
 [ 0.09759349  0.10190868  0.07812747  0.10353436  0

INFO:tensorflow:global_step/sec: 5.5176
INFO:tensorflow:probabilities = [[ 0.10811628  0.10780218  0.09476008  0.09638593  0.09052903  0.09500952
   0.10157824  0.1041925   0.09094661  0.11067966]
 [ 0.09690137  0.10202911  0.07893694  0.10895382  0.09949389  0.07935346
   0.10902097  0.11311653  0.0955118   0.1166821 ]
 [ 0.1182059   0.0858143   0.08768509  0.110851    0.09283395  0.10590988
   0.0966623   0.09521218  0.10116162  0.10566375]
 [ 0.10184009  0.10870904  0.0977352   0.09855842  0.1030781   0.0863196
   0.0975609   0.09815034  0.09758983  0.11045852]
 [ 0.1061001   0.11258838  0.08029126  0.09618959  0.09044762  0.0977821
   0.09769025  0.10935709  0.08530158  0.12425204]
 [ 0.0904496   0.11088568  0.09201685  0.11422714  0.10388418  0.08732731
   0.09905537  0.1012603   0.08782906  0.11306452]
 [ 0.08549113  0.11311106  0.0875832   0.10411039  0.10013884  0.10237273
   0.10710135  0.09850511  0.09897742  0.1026088 ]
 [ 0.09869584  0.11242255  0.08847477  0.11673146  0.09

INFO:tensorflow:step = 101, loss = 2.2816 (18.125 sec)
INFO:tensorflow:probabilities = [[ 0.09129432  0.09795378  0.10111601  0.10367373  0.10171517  0.09459163
   0.11896713  0.06813733  0.10351048  0.11904049]
 [ 0.0796556   0.10773756  0.09030923  0.11523972  0.1019275   0.08564501
   0.10700791  0.1002906   0.09085932  0.12132753]
 [ 0.10294812  0.09597921  0.10742754  0.08804995  0.10100242  0.10580461
   0.09796625  0.09065775  0.10488193  0.10528229]
 [ 0.08736336  0.10477475  0.08525138  0.11912403  0.0952147   0.08136418
   0.09600613  0.10534831  0.09857332  0.12697987]
 [ 0.08905417  0.09685085  0.0906454   0.10745021  0.10311291  0.08671013
   0.11219094  0.09691662  0.10638908  0.11067973]
 [ 0.08873089  0.103608    0.08936492  0.11001322  0.09534089  0.08263301
   0.09528019  0.09873553  0.11368464  0.12260869]
 [ 0.08486448  0.10022961  0.09174093  0.10390821  0.10397821  0.09723126
   0.11140743  0.096648    0.10592387  0.10406799]
 [ 0.0956801   0.11117201  0.08483022 

INFO:tensorflow:global_step/sec: 5.50871
INFO:tensorflow:probabilities = [[ 0.09789349  0.10429684  0.09157127  0.10763139  0.10987165  0.08163263
   0.09623469  0.09609863  0.10137542  0.11339398]
 [ 0.09082388  0.11694154  0.07246285  0.10826045  0.10243426  0.09800166
   0.10489603  0.09706356  0.10122355  0.10789223]
 [ 0.09137676  0.11104246  0.09715757  0.10597957  0.09689826  0.09858885
   0.10698524  0.08879233  0.09626583  0.10691317]
 [ 0.09784336  0.09030968  0.09583468  0.09976064  0.09780969  0.09749896
   0.10470632  0.10245536  0.10572655  0.10805468]
 [ 0.09714635  0.10278174  0.09819259  0.10940488  0.09582102  0.10451829
   0.10129674  0.08459843  0.0954196   0.11082035]
 [ 0.08938796  0.104504    0.09452561  0.11332639  0.09452668  0.07848876
   0.10201769  0.08991425  0.10469775  0.12861091]
 [ 0.09227843  0.10509273  0.09996767  0.12357328  0.08844172  0.09392329
   0.09032621  0.09825048  0.10079901  0.10734721]
 [ 0.11258169  0.10124458  0.09258473  0.10863984  0

...

INFO:tensorflow:global_step/sec: 5.3894
INFO:tensorflow:probabilities = [[ 0.00035915  0.00008194  0.00000821  0.0000938   0.00009259  0.99705446
   0.00070498  0.00000909  0.00158994  0.00000583]
 [ 0.00427625  0.00000449  0.01329439  0.9498381   0.00000071  0.01857629
   0.00000399  0.00000648  0.01377628  0.00022313]
 [ 0.00000829  0.00049405  0.01612618  0.00069409  0.05034249  0.00003848
   0.00004516  0.91937357  0.00023765  0.01263998]
 [ 0.          0.00000057  0.0000021   0.00012416  0.00000005  0.00000005
   0.          0.99979049  0.00000027  0.00008232]
 [ 0.00000011  0.00009988  0.99923944  0.00062421  0.          0.00000007
   0.00000158  0.00000001  0.00003483  0.        ]
 [ 0.00000262  0.00002236  0.0002414   0.00016761  0.00406611  0.00000712
   0.00000042  0.0016839   0.00159664  0.99221182]
 [ 0.00000394  0.00159179  0.00000065  0.00241291  0.00054351  0.00009491
   0.00000003  0.0079025   0.00057796  0.98687172]
 [ 0.00000076  0.00008452  0.99960214  0.00021845  0.

INFO:tensorflow:step = 19901, loss = 0.120205 (18.557 sec)
INFO:tensorflow:probabilities = [[ 0.00000002  0.00001198  0.00000982  0.00201958  0.005224    0.00069671
   0.0000004   0.0006791   0.00185485  0.9895035 ]
 [ 0.83226329  0.00007852  0.00168483  0.1474994   0.00000116  0.01768619
   0.00069031  0.00002943  0.00004122  0.00002566]
 [ 0.00011148  0.00001858  0.00002533  0.00005547  0.00247759  0.69377249
   0.30349806  0.00000011  0.00004071  0.00000015]
 [ 0.00000002  0.00000102  0.00000263  0.997778    0.00000006  0.00106731
   0.00000001  0.00114001  0.00000407  0.00000689]
 [ 0.02167338  0.00322229  0.11925363  0.04942991  0.5357607   0.01345192
   0.01777738  0.03776977  0.03489136  0.1667697 ]
 [ 0.00000149  0.00006081  0.99879187  0.00104655  0.00000003  0.0000018
   0.00000077  0.00000433  0.00009244  0.00000001]
 [ 0.00000001  0.00000011  0.00000008  0.00000078  0.99922478  0.00006532
   0.00000641  0.00000759  0.00000164  0.00069316]
 [ 0.00004048  0.00000536  0.004147

INFO:tensorflow:Saving checkpoints for 20000 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:Loss for final step: 0.073758.
INFO:tensorflow:Starting evaluation at 2018-03-19-07:59:44
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model/model.ckpt-20000
INFO:tensorflow:Finished evaluation at 2018-03-19-07:59:49
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.9699, global_step = 20000, loss = 0.10361
{'accuracy': 0.96990001, 'global_step': 20000, 'loss': 0.10361025}


SystemExit: 

/Users/leosea/anaconda/envs/tensorflow/lib/python3.5/site-packages/IPython/core/interactiveshell.py:2870: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)
